In [8]:
from rdkit import Chem
from rdkit.Chem import rdMolDescriptors
import urllib2 

In [13]:
smiles = ['c1cC(=O)c(C)cN1',
          'C(=O)(O)Cc1ccccc1C(=O)NC(Cl)N', 
          'CN(C)CC/C=C1C2=C(C=CC=C2)OCC3=C/1C=CC=C3 ', 
          'O=S(=O)(c3ccc(n1nc(cc1c2ccc(cc2)C)C(F)(F)F)cc3)N'
         ]
mols = [Chem.MolFromSmiles(m) for m in smiles]

In [14]:
pattyFileURL = 'http://tripod.nih.gov/files/patty.rules'
def parsePattyFile():
    rules = []
    patty = urllib2.urlopen(pattyFileURL)
    for line in patty:
        if not line:
            continue
        if line.startswith('#'):
            continue
        pattern = line.split()
        if len(pattern) > 0:
            rules.append([Chem.MolFromSmarts(pattern[0]),pattern[1]])
    intMap = {n:i for i, n in enumerate(set([n for _, n in rules]))}  
    for i in range(len(rules)):
        rules[i][1]=intMap[rules[i][1]]
    return rules, intMap

pattyRules, pattyIntMap = parsePattyFile()
def getPattyInvariant(mol):
    mMatch = [0] * mol.GetNumAtoms()
    for p, n in pattyRules:
        match = mol.GetSubstructMatches(p)
        if match:
            for m in match:
                mMatch[m[0]] = n
    return mMatch

In [15]:
for mol in mols:
    desc = rdMolDescriptors.GetAtomPairFingerprint(mol, atomInvariants=getPattyInvariant(mol))
    print len(desc.GetNonzeroElements().values()), sum(desc.GetNonzeroElements().values())

14 28
52 120
33 210
62 325
